# Hafta 6: Model Dağıtım Stratejileri (API & Konteynerler)

**Dersin Hedefleri:**
1.  Model dağıtımının (deployment) ne anlama geldiğini ve MLOps yaşam döngüsündeki yerini anlamak.
2.  Bir makine öğrenmesi modelini, bir API (Application Programming Interface) olarak sunmanın mantığını kavramak.
3.  **FastAPI** kütüphanesini kullanarak yüksek performanslı bir tahmin (prediction) API'si oluşturmak.
4.  **Docker** kullanarak modelimizi ve tüm bağımlılıklarını taşınabilir bir konteynere paketlemek.
5.  "Benim makinemde çalışıyordu" problemini konteynerleştirme ile kalıcı olarak çözmek.

## 1. Model Dağıtımı Nedir?

Bir makine öğrenmesi modeli, `.pkl`, `.h5` gibi bir dosyada durduğu sürece kimseye değer katmaz. **Model Dağıtımı**, eğitilmiş bir modeli, son kullanıcıların veya diğer yazılım sistemlerinin tahminler almak için erişebileceği bir üretim ortamına yerleştirme sürecidir.

En yaygın dağıtım şekli, modeli bir **web servisi** olarak sunmaktır. Bu servis, belirli bir ağ adresine (endpoint) gönderilen verilere karşılık olarak modelin tahminini döndürür. Bu iletişim genellikle bir API aracılığıyla sağlanır.

## 2. FastAPI ile Bir Tahmin API'si Oluşturma

**FastAPI**, modern, hızlı (yüksek performanslı), web API'leri oluşturmak için kullanılan bir Python kütüphanesidir. `pydantic` (Hafta 2'den hatırlayalım) ve asenkron yetenekleri sayesinde ML modellerini sunmak için mükemmel bir seçimdir.

**Kurulum:**
```bash
pip install "fastapi[all]"
```
Bu komut, FastAPI'yi ve `uvicorn` adında bir ASGI sunucusunu kurar.

### Uygulama: Churn Modelimiz için API Yazma

Hafta 4'te `MLflow` ile eğittiğimiz ve kaydettiğimiz bir modeli şimdi bir API ile dünyaya açalım.

**Proje Yapısı:**
```
.
├── app/
│   ├── main.py             <-- FastAPI uygulamamız
│   ├── model.pkl           <-- Eğitilmiş modelimiz
│   └── requirements.txt
├── Dockerfile              <-- Konteyner tarifimiz
```

In [ ]:
requirements_content = """fastapi
uvicorn
scikit-learn
joblib
pandas
pydantic
"""
import os
requirements_path = os.path.join(app_dir, "requirements.txt")
with open(requirements_path, "w") as f:
    f.write(requirements_content)
print(f"✓ requirements.txt oluşturuldu: {requirements_path}")

### Adım 4: `requirements.txt` Dosyasını Oluşturma

API'nin çalışması için gerekli tüm Python paketlerini listeleyen dosyayı oluşturuyoruz.

In [ ]:
main_py_content = """
import joblib
import pandas as pd
from fastapi import FastAPI
from pydantic import BaseModel

# 1. FastAPI uygulamasını başlat
app = FastAPI(title="Churn Prediction API", version="1.0")

# 2. Model dosyasını yükle
# Bu, uygulama başladığında sadece bir kez yapılır.
model = joblib.load('model.pkl')

# 3. Girdi verisinin şemasını Pydantic ile tanımla
# Bu, API'ye gönderilecek JSON verisinin yapısını zorunlu kılar.
class CustomerFeatures(BaseModel):
    age: int
    total_spent: float
    membership_days: int
    
    class Config:
        schema_extra = {
            "example": {
                "age": 45,
                "total_spent": 550.75,
                "membership_days": 850
            }
        }

# 4. API'nin ana endpoint'ini oluştur
@app.get("/")
def read_root():
    return {"message": "Churn Prediction API'sine hoş geldiniz!"}

# 5. Tahmin endpoint'ini oluştur
# Bu endpoint, POST isteklerini kabul eder ve /predict adresinde çalışır.
@app.post("/predict/")
def predict_churn(features: CustomerFeatures):
    # Gelen Pydantic objesini modelin beklediği DataFrame'e çevir
    input_df = pd.DataFrame([features.dict()])
    
    # Tahmini yap
    prediction_proba = model.predict_proba(input_df)[0][1] # Churn olma olasılığı
    prediction = model.predict(input_df)[0]
    
    return {
        "churn_probability": float(prediction_proba),
        "prediction": int(prediction)
    }
"""

# Dosyaya yaz
main_py_path = os.path.join(app_dir, "main.py")
with open(main_py_path, "w") as f:
    f.write(main_py_content)
print(f"✓ FastAPI uygulaması oluşturuldu: {main_py_path}")

### Adım 3: FastAPI Uygulamasını (`main.py`) Oluşturma

Bu adımda API uygulamamızın ana kodunu yazacağız. Bu kod:
1. FastAPI instance'ı oluşturur
2. Model dosyasını yükler
3. Girdi verisinin şemasını Pydantic ile tanımlar
4. Tahmin endpoint'lerini tanımlar

In [ ]:
import joblib
import pandas as pd
from sklearn.linear_model import LogisticRegression

# Eğitim verisi oluştur (customer churn prediction için)
X_train_dummy = pd.DataFrame({
    'age': [25, 45, 35, 50],
    'total_spent': [100, 500, 250, 800],
    'membership_days': [100, 1000, 400, 1500]
})
y_train_dummy = pd.Series([0, 1, 0, 1])  # 0: Churn olmadı, 1: Churn oldu

# Model eğit
model = LogisticRegression()
model.fit(X_train_dummy, y_train_dummy)

# Modeli dosyaya kaydet
model_path = os.path.join(app_dir, "model.pkl")
joblib.dump(model, model_path)
print(f"✓ Model kaydedildi: {model_path}")

### Adım 2: Eğitilmiş Model Oluşturma ve Kaydetme

Gerçek dünyada bu model MLflow'dan veya başka bir model registry'den indirilir. Bu örnekte basit bir Logistic Regression modeli eğitip kaydediyoruz.

### API'yi Yerel Olarak Çalıştırma

Yukarıdaki yapı hazır olduğunda, API'yi çalıştırmak için:
1.  Terminali açın ve `hafta6_projesi/app` dizinine gidin.
2.  Aşağıdaki komutu çalıştırın:
    ```bash
    uvicorn main:app --reload
    ```
    *   `main`: `main.py` dosyasının adı.
    *   `app`: Dosya içinde `app = FastAPI()` ile oluşturulan obje.
    *   `--reload`: Kodda her değişiklik yaptığınızda sunucuyu otomatik olarak yeniden başlatır.
3.  Tarayıcınızda `http://127.0.0.1:8000` adresini açın. "Hoş geldiniz" mesajını göreceksiniz.
4.  `http://127.0.0.1:8000/docs` adresini açın. FastAPI'nin otomatik olarak oluşturduğu interaktif API dokümantasyonunu (Swagger UI) göreceksiniz. Buradan `/predict` endpoint'ini test edebilir, örnek veriler gönderebilir ve dönen yanıtı görebilirsiniz.

## 3. Docker ile Konteynerleştirme

API'miz yerel makinemizde çalışıyor. Ancak bunu başka bir sunucuya veya bir bulut platformuna nasıl taşırız? Gerekli tüm kütüphanelerin (fastapi, sklearn vb.) orada da kurulu olduğundan nasıl emin oluruz?

**Docker**, bu sorunu çözer. Uygulamamızı, tüm bağımlılıkları ve işletim sistemi seviyesindeki gereksinimleri ile birlikte **konteyner** adı verilen izole bir pakete koymamızı sağlar. Bu konteyner, Docker'ın çalıştığı her yerde **aynı şekilde** çalışır.

### `Dockerfile` Yazma

`Dockerfile`, Docker'a bizim imajımızı (image) nasıl oluşturacağını söyleyen bir tarif dosyasıdır.

In [ ]:
# --- Dockerfile Oluşturma ---
dockerfile_content = """
# Adım 1: Temel imajı belirle. Uygulamamız Python 3.9 gerektiriyor.
FROM python:3.9-slim

# Adım 2: Çalışma dizinini ayarla. Konteyner içindeki varsayılan klasör.
WORKDIR /code

# Adım 3: Bağımlılıkları kopyala ve kur.
# Önce sadece requirements'ı kopyalamak, Docker katman önbelleğini (layer cache)
# verimli kullanır. Kod değişse bile bağımlılıklar değişmediyse bu adım tekrar çalışmaz.
COPY ./app/requirements.txt /code/requirements.txt
RUN pip install --no-cache-dir --upgrade -r /code/requirements.txt

# Adım 4: Uygulama kodunu konteynere kopyala.
COPY ./app /code/app

# Adım 5: Uygulamanın çalışacağı portu belirt.
EXPOSE 8000

# Adım 6: Konteyner başladığında çalışacak olan komut.
# FastAPI sunucusunu başlatıyoruz. 0.0.0.0 host'u, konteynerin dışarıdan erişilebilir olmasını sağlar.
CMD ["uvicorn", "app.main:app", "--host", "0.0.0.0", "--port", "8000"]
"""
dockerfile_path = os.path.join(project_root, "Dockerfile")
with open(dockerfile_path, "w") as f:
    f.write(dockerfile_content)

print(f"Dockerfile şuraya oluşturuldu: {dockerfile_path}")
print("\n--- Dockerfile İçeriği ---")
print(dockerfile_content)

### Docker İmajı Oluşturma ve Konteyneri Çalıştırma

Docker'ın makinenizde kurulu olduğunu varsayarsak, aşağıdaki komutlar kullanılır:

1.  **İmajı Oluşturma (Build):**
    Terminalde `hafta6_projesi` kök dizinindeyken:
    ```bash
    docker build -t churn-api:1.0 .
    ```
    *   `-t churn-api:1.0`: İmajımıza bir isim (`churn-api`) ve etiket (`1.0`) verir.
    *   `.`: Dockerfile'ın bulunduğu mevcut dizini belirtir.

2.  **Konteyneri Çalıştırma (Run):**
    İmaj oluşturulduktan sonra, ondan bir konteyner başlatabiliriz:
    ```bash
    docker run -p 8000:8000 churn-api:1.0
    ```
    *   `-p 8000:8000`: Yerel makinenizin 8000 portunu, konteynerin 8000 portuna yönlendirir (map).

Artık API'niz, makinenizin geri kalanından tamamen izole bir ortamda çalışıyor. Tarayıcınızdan yine `http://127.0.0.1:8000/docs` adresine giderek aynı interaktif dokümantasyonu görebilirsiniz.

### Alıştırma: API'ye Yeni Bir Özellik Ekleme

1.  `app/main.py` dosyasını açın.
2.  `/model-info` adında yeni bir GET endpoint'i ekleyin.
3.  Bu endpoint, yüklü olan model hakkında basit bilgiler döndürmelidir. Örneğin, modelin `scikit-learn` sınıfının adını (`model.__class__.__name__`) ve modelin eğitilirken gördüğü özelliklerin listesini (`model.feature_names_in_`) döndüren bir JSON yanıtı oluşturun.
4.  Değişikliklerinizi kaydedin.
5.  Eğer `uvicorn`'u `--reload` ile çalıştırıyorsanız, değişikliğin anında yansıdığını `/docs` sayfasını yenileyerek görün.
6.  Eğer Docker kullanıyorsanız, imajı yeniden build edip konteyneri tekrar çalıştırarak değişikliğin konteynerize edilmiş uygulamaya nasıl yansıtıldığını gözlemleyin.

### Adım 1: Gerekli Bilgileri Anlama

Model objelerinden alabileceğimiz meta veriler:

1. **`model.__class__.__name__`**: Modelin sınıf adı (örn: "LogisticRegression")
2. **`model.feature_names_in_`**: Model eğitilirken kullanılan özellik isimleri (scikit-learn 1.0+)
3. **`model.n_features_in_`**: Özellik sayısı

**Not:** Tüm scikit-learn modelleri `feature_names_in_` özelliğine sahip değildir. Model DataFrame ile eğitilmişse bu özellik otomatik olarak eklenir.

### Alıştırma Özeti

Bu alıştırmada öğrendikleriniz:

1. **FastAPI Endpoint Anatomisi:**
   - `@app.get("/endpoint-path")` decorator'ü ile GET endpoint tanımlama
   - Fonksiyon docstring'lerinin otomatik dokümantasyona eklenmesi
   - Python dictionary döndürerek JSON response oluşturma

2. **Model Introspection:**
   - `__class__.__name__`: Nesnenin sınıf ismini alma
   - `hasattr()`: Bir nesnenin belirli bir özelliğe sahip olup olmadığını kontrol etme
   - scikit-learn model özelliklerine erişim

3. **Development Workflow:**
   - Hot-reload ile hızlı iterasyon (`--reload` flag'i)
   - Swagger UI (`/docs`) ile interaktif test
   
4. **Production Workflow:**
   - Docker imajını yeniden build etme
   - Semantic versioning (1.0 → 1.1)
   - İmaj etiketleme best practices

### Adım 4: Docker İmajını Güncelleme

Değişiklikleri Docker konteynerine yansıtmak için imajı yeniden build etmeniz gerekir:

```bash
cd hafta6_projesi
docker build -t churn-api:1.1 .
docker run -p 8000:8000 churn-api:1.1
```

**Önemli Gözlem:** Versiyon numarasını `1.0`'dan `1.1`'e çıkardık. Bu, sürüm kontrolünde en iyi pratiktir.

**Alternatif:** Aynı etiketi kullanarak yeniden build edebilirsiniz:
```bash
docker build -t churn-api:1.0 .
```
Ancak bu, önceki imajın üzerine yazacaktır.

In [ ]:
# Test kodu (API çalışıyorsa kullanabilirsiniz)
# import requests
# 
# response = requests.get("http://127.0.0.1:8000/model-info")
# print("Status Code:", response.status_code)
# print("Response:")
# print(response.json())

# Beklenen çıktı:
print("""
Beklenen çıktı:
{
  "model_type": "LogisticRegression",
  "n_features": 3,
  "feature_names": ["age", "total_spent", "membership_days"]
}
""")

### Adım 3: Endpoint'i Test Etme

Endpoint'in çalışıp çalışmadığını kontrol etmek için `requests` kütüphanesini kullanabiliriz.

**Not:** API'nin çalışıyor olması gerekir. Yukarıdaki hücreyi çalıştırdıktan sonra, terminalde:
```bash
cd hafta6_projesi/app
uvicorn main:app --reload
```
komutunu çalıştırın.

In [ ]:
# Alıştırma çözümü: /model-info endpoint'i ekleme

updated_main_py = """
import joblib
import pandas as pd
from fastapi import FastAPI
from pydantic import BaseModel

app = FastAPI(title="Churn Prediction API", version="1.0")
model = joblib.load('model.pkl')

class CustomerFeatures(BaseModel):
    age: int
    total_spent: float
    membership_days: int
    
    class Config:
        schema_extra = {
            "example": {
                "age": 45,
                "total_spent": 550.75,
                "membership_days": 850
            }
        }

@app.get("/")
def read_root():
    return {"message": "Churn Prediction API'sine hoş geldiniz!"}

@app.post("/predict/")
def predict_churn(features: CustomerFeatures):
    input_df = pd.DataFrame([features.dict()])
    prediction_proba = model.predict_proba(input_df)[0][1]
    prediction = model.predict(input_df)[0]
    
    return {
        "churn_probability": float(prediction_proba),
        "prediction": int(prediction)
    }

# YENİ ENDPOINT: Model bilgilerini döndürür
@app.get("/model-info")
def get_model_info():
    '''
    Model hakkında meta verileri döndürür.
    
    Returns:
        dict: Model tipi, özellik sayısı ve özellik isimleri
    '''
    info = {
        "model_type": model.__class__.__name__,
        "n_features": model.n_features_in_,
    }
    
    # feature_names_in_ varsa ekle (opsiyonel)
    if hasattr(model, 'feature_names_in_'):
        info["feature_names"] = model.feature_names_in_.tolist()
    else:
        info["feature_names"] = None
    
    return info
"""

# Dosyayı güncelle
with open(os.path.join(app_dir, "main.py"), "w") as f:
    f.write(updated_main_py)

print("✓ main.py güncellendi - /model-info endpoint'i eklendi")

### Adım 2: Endpoint Kodunu Yazma

`app/main.py` dosyasına aşağıdaki endpoint'i ekleyin:

In [ ]:
# Temizlik
shutil.rmtree(project_root)

### Haftanın Özeti

Bu hafta, makine öğrenmesi modellerimizi birer laboratuvar deneyinden, kullanılabilir yazılım ürünlerine dönüştürmenin ilk ve en önemli adımını attık.

- **API'ler**, modellerimizi diğer sistemlerle konuşturan standart bir arayüz sağlar.
- **FastAPI**, Python'da yüksek performanslı ve modern API'ler oluşturmak için mükemmel bir araçtır. Otomatik veri doğrulama ve dokümantasyon gibi özellikleri geliştirme sürecini hızlandırır.
- **Docker**, uygulamalarımızı ve bağımlılıklarını izole, taşınabilir ve yeniden üretilebilir **konteynerlere** paketlememizi sağlar. Bu, MLOps'ta "her yerde aynı şekilde çalışır" garantisi için altın standarttır.

### Sonraki Adımlar

Artık çalışan ve paketlenmiş bir model servisimiz var. Peki bu servisin performansı zamanla düşerse ne olur? Gelen verinin yapısı değişirse modelimiz hala doğru tahminler yapar mı? Bir sonraki hafta, **Hafta 7: Üretim Ortamında Model İzleme ve Sürekli Teslimat (CD)**'da, bu sorulara cevap arayacağız. Canlıdaki bir modelin "sağlığını" nasıl izleyeceğimizi ve MLOps döngüsünü yeniden eğitimle nasıl tamamlayacağımızı öğreneceğiz.

---

## **Hafta 7: Üretim Ortamında Model İzleme ve Sürekli Teslimat (CD)**
```python